In [9]:
def register_call(frm,to):
    global targets_todo, from_rel
    targets_todo.add(to)
    from_rel[to].add(frm)

def parse_line(l): # Split out line to ( addr, is_jump, next_addr) or 2
    (x_addr, asm, op, *s_args ) = l.split('\t')
    addr = int(x_addr.strip().translate({ord(c): None for c in ':'}),base=16) & 0x3fffff
    #  s_args might contain an address in either [0] or [1]

    if op not in (
                  'brlt', 'brle',  'brgt',  'brge',
                  'breq', 'brne',  'brlo',  'brsh',
                  'brbc', 'brbs',  'brcc',  'brcs',
                  'brtc', 'brts',  'brvc',  'brvs',
                  'brmi', 'brpl',  'brie',  'brid',
                  'jmp',  'rjmp',  'ijmp',  'eijmp',
                  'call', 'rcall', 'icall', 'eicall',
                  'sbrc', 'sbrs', 'sbis', 'sbic', 'cpse',
                  ):
        return (addr,False,addr+2) # Too lazy to find all multi-word ops, but this case is ignored anyway
    else:
        if op not in ('jmp', 'rjmp', 'ijmp', 'eijmp',
                      'call', 'rcall', 'icall', 'eicall'): # Not a jmp, so we need to note the next instruction 
            yield (addr,True,addr+2) # next if branch not taken
        
        if op in ('sbrc', 'sbrs', 'sbis', 'sbic', 'cpse',): # Skip is a branch to addr+4 (skipping addr+2)
            yield (addr, True, addr+4)
        else:
            dest = int(s_args[1].strip().translate({ord(c): None for c in ';'}),base=16) & 0x3fffff
            yield (addr, True, dest)

In [10]:
import io
from collections import defaultdict
# Pass 1, find all control flow targets
targets_todo = set()
from_rel = defaultdict(set)
asm_lines = dict()

with io.open("from_hardware.flash.hex.dis","r",encoding='utf8',newline='\n') as f:
    
    for working_line in f:
        print(f'Working with line {working_line.strip()}')
        for (addr, is_jmp, dst) in parse_line(working_line):
            print(f'\tParsed to {addr},{is_jmp},{dst}')
            asm_lines[addr]=working_line

            if is_jmp:
                register_call(frm=addr,to=dst)
                print(f'\t\t{len(targets_todo)} targets known')
    
print(f'{len(targets_todo)} jump targets')

Working with line 0:	0c 94 60 0c 	jmp	0x18c0	;  0x18c0
	Parsed to 0,True,6336
		1 targets known
Working with line 4:	0c 94 8d 0c 	jmp	0x191a	;  0x191a
	Parsed to 4,True,6426
		2 targets known
Working with line 8:	0c 94 8d 0c 	jmp	0x191a	;  0x191a
	Parsed to 8,True,6426
		2 targets known
Working with line c:	0c 94 8d 0c 	jmp	0x191a	;  0x191a
	Parsed to 12,True,6426
		2 targets known
Working with line 10:	0c 94 8d 0c 	jmp	0x191a	;  0x191a
	Parsed to 16,True,6426
		2 targets known
Working with line 14:	0c 94 8d 0c 	jmp	0x191a	;  0x191a
	Parsed to 20,True,6426
		2 targets known
Working with line 18:	0c 94 8d 0c 	jmp	0x191a	;  0x191a
	Parsed to 24,True,6426
		2 targets known
Working with line 1c:	0c 94 8d 0c 	jmp	0x191a	;  0x191a
	Parsed to 28,True,6426
		2 targets known
Working with line 20:	0c 94 8d 0c 	jmp	0x191a	;  0x191a
	Parsed to 32,True,6426
		2 targets known
Working with line 24:	0c 94 8d 0c 	jmp	0x191a	;  0x191a
	Parsed to 36,True,6426
		2 targets known
Working with line 28:	0c 94

Working with line 6a8:	2b 31       	cpi	r18, 0x1B	; 27
Working with line 6aa:	2c 20       	and	r2, r12
Working with line 6ac:	4c 61       	ori	r20, 0x1C	; 28
Working with line 6ae:	73 74       	andi	r23, 0x43	; 67
Working with line 6b0:	20 4c       	sbci	r18, 0xC0	; 192
Working with line 6b2:	69 6e       	ori	r22, 0xE9	; 233
Working with line 6b4:	65 3a       	cpi	r22, 0xA5	; 165
Working with line 6b6:	20 00       	.word	0x0020	; ????
Working with line 6b8:	4d 31       	cpi	r20, 0x1D	; 29
Working with line 6ba:	31 30       	cpi	r19, 0x01	; 1
Working with line 6bc:	00 44       	sbci	r16, 0x40	; 64
Working with line 6be:	6f 6e       	ori	r22, 0xEF	; 239
Working with line 6c0:	65 20       	and	r6, r5
Working with line 6c2:	73 61       	ori	r23, 0x13	; 19
Working with line 6c4:	76 69       	ori	r23, 0x96	; 150
Working with line 6c6:	6e 67       	ori	r22, 0x7E	; 126
Working with line 6c8:	20 66       	ori	r18, 0x60	; 96
Working with line 6ca:	69 6c       	ori	r22, 0xC9	; 201
Working with li

Working with line dca:	00 6b       	ori	r16, 0xB0	; 176
Working with line dcc:	08 13       	cpse	r16, r24
	Parsed to 3532,True,3534
		71 targets known
	Parsed to 3532,True,3536
		72 targets known
Working with line dce:	00 58       	subi	r16, 0x80	; 128
Working with line dd0:	08 12       	cpse	r0, r24
	Parsed to 3536,True,3538
		73 targets known
	Parsed to 3536,True,3540
		74 targets known
Working with line dd2:	00 46       	sbci	r16, 0x60	; 96
Working with line dd4:	08 12       	cpse	r0, r24
	Parsed to 3540,True,3542
		75 targets known
	Parsed to 3540,True,3544
		76 targets known
Working with line dd6:	00 34       	cpi	r16, 0x40	; 64
Working with line dd8:	08 11       	cpse	r16, r8
	Parsed to 3544,True,3546
		77 targets known
	Parsed to 3544,True,3548
		78 targets known
Working with line dda:	00 23       	and	r16, r16
Working with line ddc:	08 11       	cpse	r16, r8
	Parsed to 3548,True,3550
		79 targets known
	Parsed to 3548,True,3552
		80 targets known
Working with line dde:	00 12   

Working with line 134a:	44 00       	.word	0x0044	; ????
Working with line 134c:	53 74       	andi	r21, 0x43	; 67
Working with line 134e:	6f 70       	andi	r22, 0x0F	; 15
Working with line 1350:	20 50       	subi	r18, 0x00	; 0
Working with line 1352:	72 69       	ori	r23, 0x92	; 146
Working with line 1354:	6e 74       	andi	r22, 0x4E	; 78
Working with line 1356:	00 52       	subi	r16, 0x20	; 32
Working with line 1358:	65 73       	andi	r22, 0x35	; 53
Working with line 135a:	75 6d       	ori	r23, 0xD5	; 213
Working with line 135c:	65 20       	and	r6, r5
Working with line 135e:	50 72       	andi	r21, 0x20	; 32
Working with line 1360:	69 6e       	ori	r22, 0xE9	; 233
Working with line 1362:	74 00       	.word	0x0074	; ????
Working with line 1364:	50 61       	ori	r21, 0x10	; 16
Working with line 1366:	75 73       	andi	r23, 0x35	; 53
Working with line 1368:	65 20       	and	r6, r5
Working with line 136a:	50 72       	andi	r21, 0x20	; 32
Working with line 136c:	69 6e       	ori	r22, 0xE9	

		240 targets known
	Parsed to 6784,True,6792
		240 targets known
Working with line 1a82:	81 e0       	ldi	r24, 0x01	; 1
Working with line 1a84:	90 e0       	ldi	r25, 0x00	; 0
Working with line 1a86:	03 c0       	rjmp	.+6      	;  0x1a8e
	Parsed to 6790,True,6798
		241 targets known
Working with line 1a88:	29 91       	ld	r18, Y+
Working with line 1a8a:	82 e0       	ldi	r24, 0x02	; 2
Working with line 1a8c:	90 e0       	ldi	r25, 0x00	; 0
Working with line 1a8e:	e2 2f       	mov	r30, r18
Working with line 1a90:	e0 53       	subi	r30, 0x30	; 48
Working with line 1a92:	ea 30       	cpi	r30, 0x0A	; 10
Working with line 1a94:	18 f0       	brcs	.+6      	;  0x1a9c
	Parsed to 6804,True,6806
		242 targets known
	Parsed to 6804,True,6812
		243 targets known
Working with line 1a96:	c8 1b       	sub	r28, r24
Working with line 1a98:	d9 0b       	sbc	r29, r25
Working with line 1a9a:	1c c0       	rjmp	.+56     	;  0x1ad4
	Parsed to 6810,True,6868
		243 targets known
Working with line 1a9c:	20 e0    

...

Working with line 3e3da:	86 ff       	sbrs	r24, 6
	Parsed to 254938,True,254940
		9048 targets known
	Parsed to 254938,True,254942
		9049 targets known
Working with line 3e3dc:	fc cf       	rjmp	.-8      	;  0x3e3d6
	Parsed to 254940,True,254934
		9050 targets known
Working with line 3e3de:	80 91 c0 00 	lds	r24, 0x00C0
Working with line 3e3e2:	80 64       	ori	r24, 0x40	; 64
Working with line 3e3e4:	80 93 c0 00 	sts	0x00C0, r24
Working with line 3e3e8:	08 95       	ret
Working with line 3e3ea:	0f 94 c2 f1 	call	0x3e384	;  0x3e384
	Parsed to 254954,True,254852
		9051 targets known
Working with line 3e3ee:	0f 94 dc f1 	call	0x3e3b8	;  0x3e3b8
	Parsed to 254958,True,254904
		9052 targets known
Working with line 3e3f2:	08 95       	ret
Working with line 3e3f4:	fc 01       	movw	r30, r24
Working with line 3e3f6:	90 81       	ld	r25, Z
Working with line 3e3f8:	99 23       	and	r25, r25
Working with line 3e3fa:	59 f0       	breq	.+22     	;  0x3e412
	Parsed to 254970,True,254972
		9053 target

Working with line 3e9fc:	18 c2       	rjmp	.+1072   	;  0x3ee2e
	Parsed to 256508,True,257582
		9215 targets known
Working with line 3e9fe:	96 35       	cpi	r25, 0x56	; 86
Working with line 3ea00:	09 f4       	brne	.+2      	;  0x3ea04
	Parsed to 256512,True,256514
		9216 targets known
	Parsed to 256512,True,256516
		9217 targets known
Working with line 3ea02:	45 c2       	rjmp	.+1162   	;  0x3ee8e
	Parsed to 256514,True,257678
		9218 targets known
Working with line 3ea04:	99 35       	cpi	r25, 0x59	; 89
Working with line 3ea06:	09 f0       	breq	.+2      	;  0x3ea0a
	Parsed to 256518,True,256520
		9219 targets known
	Parsed to 256518,True,256522
		9220 targets known
Working with line 3ea08:	c4 c5       	rjmp	.+2952   	;  0x3f592
	Parsed to 256520,True,259474
		9220 targets known
Working with line 3ea0a:	67 c4       	rjmp	.+2254   	;  0x3f2da
	Parsed to 256522,True,258778
		9221 targets known
Working with line 3ea0c:	83 e7       	ldi	r24, 0x73	; 115
Working with line 3ea0e:	92 ee      

Working with line 3f084:	80 93 c0 00 	sts	0x00C0, r24
Working with line 3f088:	c4 5d       	subi	r28, 0xD4	; 212
Working with line 3f08a:	de 4f       	sbci	r29, 0xFE	; 254
Working with line 3f08c:	88 81       	ld	r24, Y
Working with line 3f08e:	cc 52       	subi	r28, 0x2C	; 44
Working with line 3f090:	d1 40       	sbci	r29, 0x01	; 1
Working with line 3f092:	0f 94 0d f2 	call	0x3e41a	;  0x3e41a
	Parsed to 258194,True,255002
		9291 targets known
Working with line 3f096:	40 e2       	ldi	r20, 0x20	; 32
Working with line 3f098:	40 93 c6 00 	sts	0x00C6, r20
Working with line 3f09c:	80 91 c0 00 	lds	r24, 0x00C0
Working with line 3f0a0:	86 ff       	sbrs	r24, 6
	Parsed to 258208,True,258210
		9292 targets known
	Parsed to 258208,True,258212
		9293 targets known
Working with line 3f0a2:	fc cf       	rjmp	.-8      	;  0x3f09c
	Parsed to 258210,True,258204
		9294 targets known
Working with line 3f0a4:	80 91 c0 00 	lds	r24, 0x00C0
Working with line 3f0a8:	80 64       	ori	r24, 0x40	; 64
Working w

		9451 targets known
	Parsed to 259486,True,259556
		9452 targets known
Working with line 3f5a0:	94 30       	cpi	r25, 0x04	; 4
Working with line 3f5a2:	28 f4       	brcc	.+10     	;  0x3f5ae
	Parsed to 259490,True,259492
		9453 targets known
	Parsed to 259490,True,259502
		9454 targets known
Working with line 3f5a4:	91 30       	cpi	r25, 0x01	; 1
Working with line 3f5a6:	89 f0       	breq	.+34     	;  0x3f5ca
	Parsed to 259494,True,259496
		9455 targets known
	Parsed to 259494,True,259530
		9456 targets known
Working with line 3f5a8:	92 30       	cpi	r25, 0x02	; 2
Working with line 3f5aa:	b8 f4       	brcc	.+46     	;  0x3f5da
	Parsed to 259498,True,259500
		9457 targets known
	Parsed to 259498,True,259546
		9458 targets known
Working with line 3f5ac:	08 c0       	rjmp	.+16     	;  0x3f5be
	Parsed to 259500,True,259518
		9459 targets known
Working with line 3f5ae:	95 30       	cpi	r25, 0x05	; 5
Working with line 3f5b0:	61 f1       	breq	.+88     	;  0x3f60a
	Parsed to 259504,True,2595

Working with line 3fb22:	96 01       	movw	r18, r12
Working with line 3fb24:	2d 5f       	subi	r18, 0xFD	; 253
Working with line 3fb26:	3f 4f       	sbci	r19, 0xFF	; 255
Working with line 3fb28:	fb 01       	movw	r30, r22
Working with line 3fb2a:	10 82       	st	Z, r1
Working with line 3fb2c:	04 c0       	rjmp	.+8      	;  0x3fb36
	Parsed to 260908,True,260918
		9589 targets known
Working with line 3fb2e:	80 ec       	ldi	r24, 0xC0	; 192
Working with line 3fb30:	8a 83       	std	Y+2, r24	; 0x02
Working with line 3fb32:	22 e0       	ldi	r18, 0x02	; 2
Working with line 3fb34:	30 e0       	ldi	r19, 0x00	; 0
Working with line 3fb36:	8b e1       	ldi	r24, 0x1B	; 27
Working with line 3fb38:	80 93 c6 00 	sts	0x00C6, r24
Working with line 3fb3c:	80 91 c0 00 	lds	r24, 0x00C0
Working with line 3fb40:	86 ff       	sbrs	r24, 6
	Parsed to 260928,True,260930
		9590 targets known
	Parsed to 260928,True,260932
		9591 targets known
Working with line 3fb42:	fc cf       	rjmp	.-8      	;  0x3fb3c
	Parsed

In [12]:
for addr in sorted(targets_todo):
    print(f'{addr:05x}:\t',end='')
    print(f'from {from_rel[addr]}')

00000:	from {94328, 6426, 133766}
00004:	from {4098}
00098:	from {3734}
000a4:	from {2210}
0012c:	from {3882}
0019e:	from {4496}
002b2:	from {3140}
00304:	from {3330}
00498:	from {2198}
00520:	from {3870}
005b8:	from {3510}
00788:	from {3462}
007f0:	from {4078}
00800:	from {4094}
00820:	from {2078}
0084c:	from {2186}
0085e:	from {2140}
00860:	from {2140}
00862:	from {2144}
00864:	from {2144}
00866:	from {2148}
00868:	from {2148}
0088c:	from {2186}
008a6:	from {6308}
008d4:	from {2258}
008d6:	from {2258}
0098a:	from {4480}
00a2c:	from {2090}
00abc:	from {3200}
00b9a:	from {4492}
00c1c:	from {3098}
00c1e:	from {3098}
00c3a:	from {3128}
00c3c:	from {3128}
00c60:	from {3166}
00c62:	from {3166}
00c9e:	from {3228}
00ca0:	from {3228, 2206}
00cac:	from {2218}
00cd4:	from {3346}
00cf4:	from {3314}
00d14:	from {3346}
00d28:	from {3878}
00d44:	from {3458}
00d48:	from {6318}
00d80:	from {3454}
00d82:	from {3454}
00d84:	from {3458}
00db0:	from {3502}
00dca:	from {3528}
00dcc:	from {3528}
00dce:	fro

022de:	from {8922}
022e0:	from {8926}
022e2:	from {8926}
022ec:	from {8938}
022ee:	from {8938}
022f0:	from {8942}
022f2:	from {8942}
022f8:	from {8944}
022fe:	from {8928}
02304:	from {8962}
02306:	from {8964}
02308:	from {8964}
0230c:	from {8966}
0230e:	from {8970}
02310:	from {8974}
02312:	from {8974}
02314:	from {8956, 8950}
0231a:	from {8998}
02324:	from {8984, 8962, 8940}
02328:	from {9018, 8998}
0233c:	from {9018}
0233e:	from {9034}
02348:	from {8578, 9020}
0234c:	from {9034}
0234e:	from {8194, 8706, 8334, 8718}
02354:	from {8160}
0235e:	from {8510}
02360:	from {9064}
02368:	from {9062}
0236a:	from {9064, 9062}
02374:	from {8470}
02376:	from {9086}
0237e:	from {9084}
02380:	from {9084, 9086}
0238a:	from {8992, 9028, 8936, 8906, 8530, 8562, 8982, 9014, 8218}
0239a:	from {9112}
0239c:	from {9112}
0239e:	from {9116}
023a0:	from {9116}
023ae:	from {9132}
023ba:	from {9118}
023c6:	from {9144, 9156, 9132}
023d2:	from {9114, 9156}
023d6:	from {9168}
023e2:	from {8668, 8790}
023ea:	from {

0369a:	from {13976}
036a0:	from {14002, 13990}
036a6:	from {13988}
036a8:	from {13988}
036ae:	from {13982}
036b4:	from {14010, 14002}
036ba:	from {14008}
036bc:	from {14008}
036c8:	from {14042, 14030}
036ce:	from {14028}
036d0:	from {14028}
036d6:	from {14022}
036dc:	from {14050, 14042}
036e2:	from {14048}
036e4:	from {14048}
036ea:	from {13930, 13940}
036fc:	from {14082}
03704:	from {14082}
0372e:	from {14454}
03732:	from {14128}
03734:	from {14128}
03738:	from {14134}
0373a:	from {14134}
0373e:	from {14140}
03740:	from {14140}
03748:	from {14150}
0374c:	from {14154}
0374e:	from {14154}
03752:	from {14160}
03754:	from {14160, 14150}
03756:	from {14164}
03758:	from {14164}
03760:	from {14174}
03762:	from {14174}
0376a:	from {14184}
03772:	from {14192}
03774:	from {14192}
0377a:	from {14200}
0377c:	from {14184, 14200}
0378a:	from {14258}
03790:	from {14222}
03798:	from {14230}
0379c:	from {14230}
037a0:	from {14222}
037b4:	from {14258}
037c0:	from {14270}
037c4:	from {14282, 14294}
037c

0554c:	from {21832}
05552:	from {21840}
05556:	from {21840}
05558:	from {21792}
0555e:	from {21852}
05560:	from {21852}
05566:	from {21860}
0556c:	from {21866}
05570:	from {21866}
05576:	from {21876}
0557a:	from {21876}
0557e:	from {21860}
05584:	from {21890}
05588:	from {21890}
0558e:	from {21900}
05592:	from {21900}
05598:	from {21910}
0559c:	from {21910}
0559e:	from {21778}
055a6:	from {21924}
055aa:	from {21924}
055b2:	from {21936}
055b8:	from {21942}
055bc:	from {21942}
055be:	from {128168, 128264, 128216}
055c2:	from {21952}
055c8:	from {21958}
055cc:	from {21958}
055d2:	from {21968}
055d6:	from {21968}
055da:	from {21952}
055e0:	from {21982}
055e4:	from {21982}
055ea:	from {21992}
055ee:	from {21992}
055f2:	from {21936}
055fa:	from {22008}
055fe:	from {22008}
05606:	from {22020}
0560e:	from {22028}
05612:	from {22028}
05618:	from {22038}
0561c:	from {22038}
05620:	from {22020}
05628:	from {22054}
0562c:	from {22054}
05634:	from {22066}
05638:	from {22066}
0563e:	from {22076}
056

068c8:	from {26822}
0690a:	from {26822}
06922:	from {26912}
06924:	from {21902}
06930:	from {26972}
0693c:	from {26938}
0694a:	from {26938}
0695e:	from {26972}
06960:	from {21768}
0696a:	from {26984}
0697e:	from {26984}
06988:	from {27014}
0698a:	from {27014}
069a0:	from {21960}
069aa:	from {27048}
069be:	from {27048}
069c8:	from {27078}
069dc:	from {27078}
069e6:	from {27108}
069fe:	from {27108}
06a08:	from {27142}
06a1c:	from {27142}
06a26:	from {27172}
06a3a:	from {27172}
06a44:	from {27202}
06a46:	from {27202}
06a5c:	from {21974}
06a68:	from {27284}
06a74:	from {27250}
06a82:	from {27250}
06a96:	from {27284}
06a98:	from {21944}
06aa2:	from {27296}
06aa4:	from {27296}
06ab6:	from {21984}
06ac0:	from {27326}
06ac2:	from {27326}
06ad4:	from {21998}
06ade:	from {27356}
06af2:	from {27356}
06afc:	from {27386}
06b1c:	from {27386}
06b26:	from {27428}
06b46:	from {27428}
06b50:	from {27470}
06b64:	from {27470}
06b6e:	from {27520, 27508}
06b74:	from {27506}
06b76:	from {27506}
06b7c:	from {

...

1cc58:	from {117846}
1cc5a:	from {117846}
1cc80:	from {117886}
1cc82:	from {117886}
1cc94:	from {117742}
1cc98:	from {117910}
1cc9a:	from {117910}
1cca2:	from {117920}
1ccc8:	from {117958}
1ccdc:	from {117958}
1ccee:	from {117978}
1ccf2:	from {117920}
1ccf6:	from {118004}
1ccf8:	from {118004}
1cd1e:	from {118044}
1cd20:	from {118044}
1cda8:	from {117912}
1cdac:	from {118186}
1cdae:	from {118186}
1cdb6:	from {118196}
1cddc:	from {118234}
1cdf0:	from {118234}
1ce02:	from {118254}
1ce06:	from {118196}
1ce0a:	from {118280}
1ce0c:	from {118280}
1ce32:	from {118320}
1ce34:	from {118320}
1cebc:	from {118188}
1cec0:	from {118462}
1cec2:	from {118462}
1ceca:	from {118472}
1cef0:	from {118510}
1cf04:	from {118510}
1cf16:	from {118530}
1cf1a:	from {118472}
1cf1e:	from {118556}
1cf20:	from {118556}
1cf46:	from {118596}
1cf48:	from {118596}
1cfdc:	from {118464}
1cfe0:	from {118750}
1cfe2:	from {118750}
1cfea:	from {118760}
1d010:	from {118798}
1d024:	from {118798}
1d036:	from {118818}
1d03a:	from {

1f51a:	from {128280}
1f51c:	from {128280}
1f524:	from {128274}
1f528:	from {128294}
1f52e:	from {128460}
1f5be:	from {128628}
1f630:	from {128888, 128804, 129176}
1f97a:	from {129400}
1f980:	from {129400}
1f994:	from {129406}
1f9a4:	from {129442}
1f9aa:	from {129442}
1f9b6:	from {129448}
1fa08:	from {129542}
1fa0e:	from {129580}
1fa28:	from {129548}
1fa2e:	from {129580}
1fa30:	from {129542}
1fa36:	from {129582}
1fa60:	from {129630}
1fa68:	from {129638}
1fa76:	from {129638}
1fa92:	from {129630}
1fa9a:	from {129680}
1fa9e:	from {129652}
1faa8:	from {129688, 129588}
1faae:	from {129708}
1fab2:	from {129708}
1faba:	from {129720}
1fabe:	from {129720}
1face:	from {129752}
1fad2:	from {129740}
1fada:	from {129752}
1fb14:	from {129810}
1fb16:	from {129810}
1fb1c:	from {129818}
1fb22:	from {129824}
1fb24:	from {129824}
1fb2a:	from {129832}
1fb30:	from {129838}
1fb32:	from {129838}
1fb38:	from {129846}
1fb3c:	from {129850}
1fb3e:	from {129850}
1fb42:	from {129856}
1fb44:	from {129856}
1fb46:	fro

20fdc:	from {135130}
20ffc:	from {135162}
21000:	from {135162}
21002:	from {135166}
2100e:	from {135180}
21010:	from {135182}
21030:	from {135214}
21034:	from {135214}
21038:	from {134928}
2103a:	from {135180, 135182, 135024, 135128, 135130}
2103e:	from {135228, 135222}
21042:	from {134978}
21044:	from {135720, 135218, 135228}
2104a:	from {134874}
2107e:	from {135292}
21082:	from {135292}
210a0:	from {135296}
210a6:	from {135332}
210b4:	from {135332}
210ba:	from {135352}
210c8:	from {135352}
210ce:	from {135372}
210dc:	from {135372}
210e2:	from {135392}
210ee:	from {135232, 135392, 135366, 135240, 135346, 135386}
210fe:	from {135420}
21108:	from {135420}
2112a:	from {135430}
21130:	from {135470}
21134:	from {135474}
21138:	from {135478}
2113e:	from {135484}
21140:	from {135484}
21142:	from {135474}
21148:	from {135494}
2114a:	from {135494}
2114e:	from {135500}
21154:	from {135506}
21156:	from {135506}
21158:	from {135478}
21176:	from {135488}
2119a:	from {135470}
211ba:	from {135500}
2

3e34c:	from {254794}
3e364:	from {254080, 253956, 254084, 253960, 254088, 253964, 254092, 253968, 254096, 253972, 254100, 253976, 254104, 253980, 254108, 253984, 254112, 253988, 254116, 253992, 254120, 253996, 254124, 254000, 254128, 254004, 254132, 254008, 254136, 254012, 254140, 254016, 254144, 254020, 254148, 254024, 254152, 254028, 254156, 254032, 254160, 254036, 254164, 254040, 254168, 254044, 254172, 254048, 254176, 254052, 254056, 254060, 254064, 254068, 254072, 254076}
3e372:	from {254848}
3e374:	from {254838}
3e378:	from {254838}
3e37c:	from {254832}
3e382:	from {254848}
3e384:	from {255232, 256898, 256732, 256764, 258628, 256614, 256358, 256680, 257096, 254954, 258794, 258284, 256594, 257010, 256660, 256824, 256634, 256794, 256700, 258366}
3e38a:	from {254900}
3e39e:	from {254876}
3e3a2:	from {254888}
3e3a8:	from {254886}
3e3aa:	from {254886}
3e3b6:	from {254876}
3e3b8:	from {256960, 255618, 256964, 257082, 256870, 257114, 256650, 256844, 254958, 256814, 256784, 258736, 25627

3f8ee:	from {260332}
3f8f0:	from {260332}
3f918:	from {260298}
3f92e:	from {260486}
3f988:	from {260486}
3f9a6:	from {260522}
3f9aa:	from {260520}
3f9ac:	from {260520}
3f9b6:	from {260272}
3f9de:	from {260600}
3f9f4:	from {260572}
3f9fa:	from {260600}
3fa20:	from {260532}
3fa34:	from {259758, 259750}
3fa6e:	from {260716}
3fa70:	from {260786}
3fab4:	from {260786}
3fab6:	from {260716}
3faea:	from {260880}
3fb12:	from {260880}
3fb22:	from {260788}
3fb2e:	from {259706, 259756, 259782, 259726}
3fb32:	from {260658, 260116, 260222}
3fb36:	from {259874, 260004, 260908, 259918, 260094}
3fb3c:	from {260930}
3fb42:	from {260928}
3fb44:	from {260928}
3fb5c:	from {260962}
3fb62:	from {260960}
3fb64:	from {260960}
3fb74:	from {260986}
3fb7a:	from {260984}
3fb7c:	from {260984}
3fb8c:	from {261010}
3fb92:	from {261008}
3fb94:	from {261008}
3fba4:	from {261034}
3fbaa:	from {261032}
3fbac:	from {261032}
3fbce:	from {261106}
3fbd4:	from {261082}
3fbda:	from {261080}
3fbdc:	from {261080}
3fbee:	from {2610

In [ ]:
asm_lines[1595]

In [ ]:
asm_lines[0xd02]

In [ ]:
asm_lines[0x304]